In [1]:
import selenium
import pandas as pd
from selenium import webdriver
from selenium.common.exceptions import StaleElementReferenceException, NoSuchElementException
import time
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
import warnings
warnings.filterwarnings('ignore')
import requests
import re

In [2]:
driver=webdriver.Chrome(r"chromedriver.exe")
driver.get("https://www.imdb.com/search/title/?genres=action&sort=user_rating,desc&title_type=feature&num_votes=25000,&pf_rd_m=A2FGELUUNOQJNL&pf_rd_p=f11158cc-b50b-4c4d-b0a2-40b32863395b&pf_rd_r=XZ8X52H1R40B7KG5SNZ9&pf_rd_s=right-6&pf_rd_t=15506&pf_rd_i=top&ref_=chttp_gnr_1")

In [3]:
#CREATING EMPTY LISTS FOR EXTRACTION OF INFORMATION

sno=[]
movie_name=[]
director_name_1=[]
director_name_2=[]
director_name_3=[]
duration=[]
year=[]
ratings=[]
metascore=[]
stars_1=[]
stars_2=[]
stars_3=[]
stars_4=[]
votes=[]
genre_1=[]
genre_2=[]
genre_3=[]
gross_collection=[]
certification=[]
url=[]

In [4]:
try:
    for page in range(0,1000):
        
        #To extract S. no. , Movie name and year
        s=driver.find_elements(By.XPATH,'//h3[@class="lister-item-header"]')
        for i in s:
            sno.append(i.text.split(".")[0])
            movie_name.append(i.text.split(".")[1].split("(")[0].strip(" "))
            year.append(i.text.split('(')[-1].strip(")"))
            
        # To extract Duration
        dur=driver.find_elements(By.XPATH,'//span[@class="runtime"]')
        for i in dur:
            duration.append(i.text.split(" ")[0])
        
        # To extract metascore
        meta=driver.find_elements(By.XPATH,'//div[@class="ratings-bar"]')
        for i in meta:
            try:
                metascore.append(i.text.split("\n")[1].split(" ")[0])
            except:
                metascore.append("Nan")

        #To extract ratings
        rat=driver.find_elements(By.TAG_NAME,'strong')
        for i in rat[2:]:
            ratings.append(i.text)
            
        # To extract director names with sub-fields.
        dire=driver.find_elements(By.XPATH,'//div[@class="lister-item-content"]')
        for i in dire:
            director_text = i.text
            directors = re.findall(r"Director[s]?:\s+(.*)", director_text)
            if directors:             
                director_name_1.append(directors[-1].split("|")[0].split(",")[0])
                try:
                    director_name_2.append(directors[-1].split("|")[0].split(",")[1])
                except:
                    director_name_2.append("nan")
                try:
                    director_name_3.append(directors[-1].split("|")[0].split(",")[2])
                except:
                    director_name_3.append("nan")


        # TO extract votes and gross collection
        v=driver.find_elements(By.XPATH,'//p[@class="sort-num_votes-visible"]')
        for i in v:
            votes.append(i.text.split(":")[1].split(" ")[1])
        for i in v:
            try:
                gross_collection.append(i.text.split("|")[1].split("$")[1].strip("M"))
            except:
                gross_collection.append("Nan")

        # To extract certification
        cer=driver.find_elements(By.XPATH,'//p[@class="text-muted "]')
        for i in cer:
            try:
                (i.text.split("|")[2]) # To verify extraction condition
                certification.append(i.text.split("|")[0])
            except:
                certification.append("Nan")

        # To extract genres with sub-fields
        gen=driver.find_elements(By.XPATH,'//span[@class="genre"]')
        for i in gen:
            genre_1.append(i.text.split(",")[0])
            try:
                genre_2.append(i.text.split(",")[1])
            except:
                genre_2.append("Nan")
            try:
                genre_3.append(i.text.split(",")[2])
            except:
                genre_3.append("Nan")


        # To extract stars names with sub-fields
        star=driver.find_elements(By.XPATH,'//div[@class="lister-item-content"]')
        for i in dire:
            director_text = i.text
            directors = re.findall(r"Director[s]?:\s+(.*)", director_text)
            if directors:    
                stars_1.append(directors[-1].split(":")[1].split(",")[0])
                try:
                    stars_2.append(directors[-1].split(":")[1].split(",")[1])
                except:
                    stars_2.append("Nan")
                try:
                    stars_3.append(directors[-1].split(":")[1].split(",")[2])
                except:
                    stars_3.append("Nan")
                try:
                    stars_4.append(directors[-1].split(":")[1].split(",")[3])
                except:
                    stars_4.append("Nan")

        # To extract URL of all movies to extract popularity data which is given inside of each movie page.
        url_t =driver.find_elements(By.XPATH, '//h3[@class="lister-item-header"]//a')
        for i in url_t:
            url.append(i.get_attribute("href"))


        search_button=driver.find_element(By.XPATH,'//a[@class="lister-page-next next-page"]')
        search_button.click()
        time.sleep(1)
except:
    print("Extraction Complete")

Extraction Complete


In [14]:
dataset1=pd.DataFrame({"S No.":sno, "MovieName":movie_name,"Duration":duration,"Year":year,"Rating":ratings,"Metascore":metascore, "Director1":director_name_1,"Director2":director_name_2,"Director3":director_name_3})
print('\033[1m'+'IMDB MOVIES DATASET1 :'+'\033[0m')
dataset1.style.set_properties(**{'text-align':'left'}).set_table_styles([ dict(selector='th', props=[('text-align', 'left')])])

IMDB MOVIES DATASET1 :


In [15]:
Dataset2=pd.DataFrame({"MovieName":movie_name, "Star1":stars_1,"Star2":stars_2,"Star3":stars_3,"Star4":stars_4,"Genre1":genre_1,"Genre2":genre_2,"Genre3":genre_3, "GrossCollection":gross_collection,"Certification":certification,"votes":votes})
print('\033[1m'+'IMDB MOVIES DATASET2 :'+'\033[0m')
Dataset2.style.set_properties(**{'text-align':'left'}).set_table_styles([ dict(selector='th', props=[('text-align', 'left')])])

IMDB MOVIES DATASET2 :


In [16]:
dataset1.to_csv('data1.csv')

In [17]:
Dataset2.to_csv('data2.csv')